In [2]:
from sklearn.feature_extraction.text import TfidfVectorizer
from konlpy.tag import Okt
import pandas as pd
from tqdm import tqdm

In [3]:
# KoNLPy의 Okt 형태소 분석기 사용
okt = Okt()

In [4]:
def tokenize(text):
    # 형태소 분석을 통해 명사만 추출
    return [word for word in okt.nouns(text) if len(word) > 1]

In [5]:
def get_keywords(text, num=10):
    # TF-IDF 벡터화기 생성
    vectorizer = TfidfVectorizer(tokenizer=tokenize, min_df=1)
    X = vectorizer.fit_transform([text])  # 문자열 전체를 하나의 문서로 처리

    # 단어와 TF-IDF 점수 매핑
    tfidf_scores = X.sum(axis=0).A1
    words = vectorizer.get_feature_names_out()

    # 단어와 TF-IDF 점수를 데이터프레임으로 변환
    tfidf_df = pd.DataFrame({'Word': words, 'TF-IDF Score': tfidf_scores})

    # TF-IDF 점수로 정렬하여 상위 num개 키워드 출력
    return tfidf_df.sort_values(by='TF-IDF Score', ascending=False).head(num)

In [6]:
def extract_keywords_from_documents(documents, top_n=10):
    # TF-IDF 벡터화기 생성
    vectorizer = TfidfVectorizer(tokenizer=tokenize, min_df=1)
    X = vectorizer.fit_transform(documents)
    
    # 단어와 TF-IDF 점수 매핑
    words = vectorizer.get_feature_names_out()
    tfidf_scores = X.toarray()
    
    # 각 문서별 키워드 추출
    keywords_per_document = []
    for i, doc_scores in tqdm(enumerate(tfidf_scores)):
        tfidf_df = pd.DataFrame({'Word': words, 'TF-IDF Score': doc_scores})
        top_keywords = tfidf_df.sort_values(by='TF-IDF Score', ascending=False).head(top_n)
        keywords_per_document.append({
            'Document': i,
            'Keywords': ', '.join(top_keywords['Word'])
        })
    
    return pd.DataFrame(keywords_per_document)

In [8]:
directory_path = '/home/osung/data/korean/modu/json'
df = pd.read_csv(directory_path+'/combined_news_T.tsv', sep='\t')

In [9]:
extract_keywords_from_documents([df.text[0]]).Keywords

1it [00:00, 705.40it/s]


0    지수, 사회, 공존, 사람, 능력, 지능지수, 다른, 성공, 위해, 동행
Name: Keywords, dtype: object

In [10]:
df.text[:10]

0    모두에게 '윈-윈 게임'이 되는 세상, 아름다운 동행 21세기는 IQ(지능지수, I...
1    자동차 타고 우주로 드라이브할까 날씨가 추워지면서 일상생활이 많이 움츠러든다. 바깥...
2    독선과 아집은 왜 생기는 걸까? <팡세>에 관한 단상 1. "인간은 자연에서, 그것...
3    "학업에 치친 청소년들도 멋진 별세계에 찾아오세요" 국내최초로 일반인들을 대상으로 ...
4    '-의' 안 써야 우리 말이 깨끗하다 (247) ㄱ. 소비의 엄청난 증가로 인해 ....
5    일본 전자의 '간판' 소니, 14년 만에 영업 적자 일본 전자산업의 '얼굴'이라 할...
6    중고 노트북도 이젠 합체하게 해 주세요! 하루가 다르게 기술 개발이 이루어지고 신제...
7    이석채 "KT-KTF 합병, 뭐가 문제냐?"정만원 "지금 독점기업 만들 때인가?" ...
8    "정보통신부가 지원합니다..."정부 팔아 거짓영업, 이게 뭡니까 며칠 전 인터넷통신...
9    밥물 끓는 냄새 전기압력밥솥이 급경사를 오르는 증기기관차처럼 헉헉거리며 스팀을 뿜어...
Name: text, dtype: object

In [11]:
get_keywords(df.text[0]).Word

138      지수
66       사회
15       공존
64       사람
33       능력
136    지능지수
35       다른
76       성공
97       위해
49       동행
Name: Word, dtype: object

In [ ]:
t_keywords = []

for doc in tqdm(df.text) :
    t_keywords.append(extract_keywords_from_documents([doc]).Keywords)

  0%|                                                | 0/382513 [00:00<?, ?it/s]
1it [00:00, 1228.56it/s]
  0%|                                     | 1/382513 [00:00<11:44:30,  9.05it/s]
1it [00:00, 1199.74it/s]
  0%|                                     | 2/382513 [00:00<19:58:28,  5.32it/s]
1it [00:00, 1253.90it/s]

1it [00:00, 1326.05it/s]
  0%|                                     | 4/382513 [00:00<11:49:55,  8.98it/s]
1it [00:00, 1285.41it/s]

1it [00:00, 1287.78it/s]

1it [00:00, 1168.66it/s]
  0%|                                      | 7/382513 [00:00<8:21:35, 12.71it/s]
1it [00:00, 1157.37it/s]

1it [00:00, 1236.53it/s]
  0%|                                     | 9/382513 [00:00<10:31:45, 10.09it/s]
1it [00:00, 36.53it/s]

1it [00:00, 1137.28it/s]
  0%|                                    | 11/382513 [00:01<10:48:06,  9.84it/s]
1it [00:00, 744.60it/s]

1it [00:00, 1158.97it/s]
  0%|                                    | 13/382513 [00:01<12:59:53,  8.17it/s]
1it [00:00, 1174.88it/s]

  0%|                                    | 249/382513 [00:20<9:43:32, 10.92it/s]
1it [00:00, 1414.61it/s]

1it [00:00, 732.25it/s]
  0%|                                    | 251/382513 [00:20<8:59:51, 11.80it/s]
1it [00:00, 1395.78it/s]

1it [00:00, 703.98it/s]
  0%|                                    | 253/382513 [00:21<8:42:23, 12.20it/s]
1it [00:00, 1175.20it/s]

1it [00:00, 713.68it/s]
  0%|                                   | 255/382513 [00:21<10:17:18, 10.32it/s]
1it [00:00, 735.84it/s]

1it [00:00, 1363.56it/s]
  0%|                                    | 257/382513 [00:21<9:52:54, 10.75it/s]
1it [00:00, 771.15it/s]

1it [00:00, 728.05it/s]
  0%|                                    | 259/382513 [00:21<8:57:42, 11.85it/s]
1it [00:00, 699.75it/s]

1it [00:00, 1328.99it/s]
  0%|                                    | 261/382513 [00:21<9:50:38, 10.79it/s]
1it [00:00, 1470.14it/s]

1it [00:00, 1501.18it/s]
  0%|                                    | 263/382513 [00:21<8:45:50, 12.12it/s]
1i

  0%|                                    | 500/382513 [00:41<9:49:22, 10.80it/s]
1it [00:00, 1192.24it/s]

1it [00:00, 1211.18it/s]
  0%|                                   | 502/382513 [00:41<11:39:47,  9.10it/s]
1it [00:00, 1334.07it/s]

1it [00:00, 1451.32it/s]
  0%|                                   | 504/382513 [00:41<10:24:35, 10.19it/s]
1it [00:00, 1413.65it/s]

1it [00:00, 1692.62it/s]
  0%|                                    | 506/382513 [00:42<8:58:10, 11.83it/s]
1it [00:00, 1368.90it/s]

1it [00:00, 84.55it/s]
  0%|                                   | 508/382513 [00:42<10:29:45, 10.11it/s]
1it [00:00, 1316.89it/s]

1it [00:00, 1234.71it/s]
  0%|                                    | 510/382513 [00:42<9:34:08, 11.09it/s]
1it [00:00, 1393.46it/s]

1it [00:00, 1513.64it/s]
  0%|                                    | 512/382513 [00:42<9:16:14, 11.45it/s]
1it [00:00, 1192.92it/s]

1it [00:00, 771.15it/s]
  0%|                                   | 514/382513 [00:42<11:46:45,  9.01it/s

1it [00:00, 1518.03it/s]
  0%|                                    | 751/382513 [01:03<7:42:37, 13.75it/s]
1it [00:00, 1479.99it/s]

1it [00:00, 1140.07it/s]
  0%|                                    | 753/382513 [01:03<8:44:51, 12.12it/s]
1it [00:00, 1547.14it/s]

1it [00:00, 864.45it/s]
  0%|                                    | 755/382513 [01:04<8:00:20, 13.25it/s]
1it [00:00, 1399.03it/s]

1it [00:00, 1356.50it/s]
  0%|                                    | 757/382513 [01:04<7:38:21, 13.88it/s]
1it [00:00, 853.02it/s]

1it [00:00, 1087.45it/s]
  0%|                                    | 759/382513 [01:04<9:13:12, 11.50it/s]
1it [00:00, 1391.61it/s]

1it [00:00, 1284.23it/s]
  0%|                                    | 761/382513 [01:04<9:15:53, 11.45it/s]
1it [00:00, 1347.35it/s]

1it [00:00, 1546.00it/s]
  0%|                                    | 763/382513 [01:04<9:00:58, 11.76it/s]
1it [00:00, 1172.25it/s]

1it [00:00, 1444.32it/s]
  0%|                                    | 765/382513

  0%|                                   | 1003/382513 [01:25<7:45:54, 13.65it/s]
1it [00:00, 1092.55it/s]

1it [00:00, 1154.50it/s]
  0%|                                   | 1005/382513 [01:25<9:13:14, 11.49it/s]
1it [00:00, 1343.04it/s]

1it [00:00, 525.27it/s]
  0%|                                   | 1007/382513 [01:25<8:22:25, 12.66it/s]
1it [00:00, 1355.19it/s]

1it [00:00, 1167.68it/s]
  0%|                                  | 1009/382513 [01:26<10:21:18, 10.23it/s]
1it [00:00, 1256.53it/s]

1it [00:00, 791.68it/s]
  0%|                                   | 1011/382513 [01:26<9:58:18, 10.63it/s]
1it [00:00, 1341.32it/s]

1it [00:00, 1273.32it/s]
  0%|                                   | 1013/382513 [01:26<9:23:55, 11.28it/s]
1it [00:00, 1397.17it/s]

1it [00:00, 998.17it/s]
  0%|                                  | 1015/382513 [01:26<10:02:24, 10.55it/s]
1it [00:00, 1155.46it/s]

1it [00:00, 1560.96it/s]
  0%|                                   | 1017/382513 [01:26<9:22:01, 11.31it/s

...

1it [00:00, 475.92it/s]
 35%|██████████▊                    | 133785/382513 [2:45:55<8:51:45,  7.80it/s]
1it [00:00, 1403.72it/s]

1it [00:00, 1746.17it/s]

1it [00:00, 1845.27it/s]
 35%|██████████▊                    | 133788/382513 [2:45:55<7:13:16,  9.57it/s]
1it [00:00, 1873.29it/s]

1it [00:00, 1901.32it/s]

1it [00:00, 1912.59it/s]

1it [00:00, 1819.65it/s]

1it [00:00, 1815.72it/s]
 35%|██████████▊                    | 133793/382513 [2:45:55<5:06:07, 13.54it/s]
1it [00:00, 1664.41it/s]

1it [00:00, 1738.21it/s]

1it [00:00, 1501.18it/s]
 35%|██████████▊                    | 133796/382513 [2:45:55<4:28:57, 15.41it/s]
1it [00:00, 1624.44it/s]

1it [00:00, 1585.75it/s]

1it [00:00, 1880.85it/s]
 35%|██████████▊                    | 133799/382513 [2:45:55<3:55:44, 17.58it/s]
1it [00:00, 1870.79it/s]

1it [00:00, 512.50it/s]

1it [00:00, 1693.98it/s]
 35%|██████████▊                    | 133802/382513 [2:45:56<8:41:41,  7.95it/s]
1it [00:00, 1823.61it/s]

1it [00:00, 1889.33it/s]

1i

1it [00:00, 1953.56it/s]
 35%|██████████▊                    | 134121/382513 [2:46:25<4:40:52, 14.74it/s]
1it [00:00, 1990.65it/s]

1it [00:00, 1995.39it/s]

1it [00:00, 68.55it/s]

1it [00:00, 1724.63it/s]
 35%|██████████▊                    | 134125/382513 [2:46:25<3:58:11, 17.38it/s]
1it [00:00, 1771.99it/s]

1it [00:00, 1679.74it/s]

1it [00:00, 1224.97it/s]
 35%|██████████▊                    | 134128/382513 [2:46:26<8:38:13,  7.99it/s]
1it [00:00, 1481.56it/s]

1it [00:00, 1585.15it/s]

1it [00:00, 1897.02it/s]
 35%|██████████▊                    | 134131/382513 [2:46:26<7:03:27,  9.78it/s]
1it [00:00, 1956.30it/s]

1it [00:00, 1529.09it/s]

1it [00:00, 1976.58it/s]

1it [00:00, 1860.83it/s]
 35%|██████████▊                    | 134135/382513 [2:46:26<5:25:43, 12.71it/s]
1it [00:00, 1843.65it/s]

1it [00:00, 1796.28it/s]

1it [00:00, 1864.14it/s]
 35%|██████████▊                    | 134138/382513 [2:46:26<4:43:04, 14.62it/s]
1it [00:00, 1917.83it/s]

1it [00:00, 1885.93it/s]

1i

 35%|██████████▉                    | 134456/382513 [2:46:56<5:46:01, 11.95it/s]
1it [00:00, 1888.48it/s]

1it [00:00, 1909.97it/s]

1it [00:00, 1939.11it/s]
 35%|██████████▉                    | 134459/382513 [2:46:56<4:51:19, 14.19it/s]
1it [00:00, 474.52it/s]

1it [00:00, 1601.49it/s]

1it [00:00, 1758.62it/s]
 35%|██████████▉                    | 134462/382513 [2:46:57<9:20:23,  7.38it/s]
1it [00:00, 1403.72it/s]

1it [00:00, 1728.90it/s]

1it [00:00, 1708.47it/s]
 35%|██████████▉                    | 134465/382513 [2:46:57<7:34:20,  9.10it/s]
1it [00:00, 1542.02it/s]

1it [00:00, 1851.79it/s]

1it [00:00, 65.05it/s]
 35%|██████████▉                    | 134468/382513 [2:46:57<6:09:25, 11.19it/s]
1it [00:00, 1923.99it/s]

1it [00:00, 1964.55it/s]

1it [00:00, 1961.79it/s]

1it [00:00, 1958.13it/s]
 35%|██████████▉                    | 134472/382513 [2:46:57<4:44:14, 14.54it/s]
1it [00:00, 1963.63it/s]

1it [00:00, 1913.46it/s]

1it [00:00, 474.42it/s]
 35%|██████████▉              

1it [00:00, 1863.31it/s]
 35%|██████████▉                    | 134793/382513 [2:47:27<6:15:38, 10.99it/s]
1it [00:00, 1687.85it/s]

1it [00:00, 1563.87it/s]

1it [00:00, 1894.45it/s]
 35%|██████████▉                    | 134796/382513 [2:47:27<5:17:44, 12.99it/s]
1it [00:00, 1947.22it/s]

1it [00:00, 1968.23it/s]

1it [00:00, 1971.93it/s]

1it [00:00, 1895.30it/s]

1it [00:00, 1910.84it/s]
 35%|██████████▉                    | 134801/382513 [2:47:27<3:56:23, 17.46it/s]
1it [00:00, 67.24it/s]

1it [00:00, 1575.03it/s]

1it [00:00, 1573.26it/s]

1it [00:00, 492.98it/s]
 35%|██████████▉                    | 134805/382513 [2:47:28<8:01:50,  8.57it/s]
1it [00:00, 1598.44it/s]

1it [00:00, 1837.99it/s]

1it [00:00, 1892.74it/s]

1it [00:00, 1931.97it/s]
 35%|██████████▉                    | 134809/382513 [2:47:28<6:15:49, 10.98it/s]
1it [00:00, 1943.61it/s]

1it [00:00, 1969.16it/s]

1it [00:00, 1993.49it/s]

1it [00:00, 1954.48it/s]

1it [00:00, 1772.74it/s]
 35%|██████████▉                

1it [00:00, 1972.86it/s]

1it [00:00, 1975.65it/s]

1it [00:00, 1998.24it/s]


In [14]:
len(t_keywords)

382513

In [15]:
t_keywords[:10]

[0    지수, 사회, 공존, 사람, 능력, 지능지수, 다른, 성공, 위해, 동행
 Name: Keywords, dtype: object,
 0    우주, 센터, 나로, 고흥, 나로도, 발사, 해변, 위성, 소록도, 발사체
 Name: Keywords, dtype: object,
 0    인간, 독선, 아집, 파스칼, 자신, 사회, 우주, 때문, 사람, 자연
 Name: Keywords, dtype: object,
 0    시민, 천문대, 천문학, 사람, 대해, 교육, 과장, 최초, 우주, 천문
 Name: Keywords, dtype: object,
 0    주제, 강의, 감촉, 촉감, 소비, 때문, 화석연료, 토씨, 한자, 증가
 Name: Keywords, dtype: object,
 0    소니, 업적, 기록, 일본, 전자, 시장, 미국, 영업, 부진, 적자
 Name: Keywords, dtype: object,
 0    노트북, 사용, 액정, 부품, 컴퓨터, 삼보, 고장, 에버라텍, 중고, 교체
 Name: Keywords, dtype: object,
 0    합병, 사장, 시장, 경쟁, 통신, 독점, 텔레콤, 유선, 이석채, 대해
 Name: Keywords, dtype: object,
 0    회선, 인터넷, 정부, 사용, 위약금, 지원, 위해, 유치, 회원, 변경
 Name: Keywords, dtype: object,
 0    밥물, 냄새, 밥솥, 가장, 세상, 시절, 저녁, 이상, 그것, 하루
 Name: Keywords, dtype: object]

In [16]:
t_keywords[0]

0    지수, 사회, 공존, 사람, 능력, 지능지수, 다른, 성공, 위해, 동행
Name: Keywords, dtype: object

In [17]:
type(t_keywords[0])

pandas.core.series.Series

In [18]:
a = t_keywords[0]

In [19]:
a

0    지수, 사회, 공존, 사람, 능력, 지능지수, 다른, 성공, 위해, 동행
Name: Keywords, dtype: object

In [20]:
a_list = a.to_list()

In [21]:
a_list

['지수, 사회, 공존, 사람, 능력, 지능지수, 다른, 성공, 위해, 동행']

In [7]:
type(a_list)

NameError: name 'a_list' is not defined

In [40]:
ass = a_list[0].split(', ')

In [41]:
ass

['지수', '사회', '공존', '사람', '능력', '지능지수', '다른', '성공', '위해', '동행']

In [22]:
type(a_list)

list

In [42]:
keyword_list = []

for s in tqdm(t_keywords) :
    sl = s.to_list()
    ss = sl[0].split(', ')     
    keyword_list.append(ss)

100%|███████████████████████████████| 382513/382513 [00:03<00:00, 104395.20it/s]


In [46]:
keyword_list

[['지수', '사회', '공존', '사람', '능력', '지능지수', '다른', '성공', '위해', '동행'],
 ['우주', '센터', '나로', '고흥', '나로도', '발사', '해변', '위성', '소록도', '발사체'],
 ['인간', '독선', '아집', '파스칼', '자신', '사회', '우주', '때문', '사람', '자연'],
 ['시민', '천문대', '천문학', '사람', '대해', '교육', '과장', '최초', '우주', '천문'],
 ['주제', '강의', '감촉', '촉감', '소비', '때문', '화석연료', '토씨', '한자', '증가'],
 ['소니', '업적', '기록', '일본', '전자', '시장', '미국', '영업', '부진', '적자'],
 ['노트북', '사용', '액정', '부품', '컴퓨터', '삼보', '고장', '에버라텍', '중고', '교체'],
 ['합병', '사장', '시장', '경쟁', '통신', '독점', '텔레콤', '유선', '이석채', '대해'],
 ['회선', '인터넷', '정부', '사용', '위약금', '지원', '위해', '유치', '회원', '변경'],
 ['밥물', '냄새', '밥솥', '가장', '세상', '시절', '저녁', '이상', '그것', '하루'],
 ['적벽대전', '조조', '유비', '제갈량', '역사', '삼국지', '주유', '전쟁', '중국', '인물'],
 ['부품', '수리', '교체', '중고', '휴대전화', '액정', '교환', '기사', '생각', '사용'],
 ['아이', '평화', '꼬리별', '사람', '전하', '이야기', '이제', '메시지', '작가', '전쟁'],
 ['휴대전화', '복제', '휴대폰', '연예인', '사생활', '핸드폰', '단말기', '자신', '등록', '전파'],
 ['난청', '소음', '청력', '정도', '경우', '노출', '대화', '소리', '손상', '음성'],
 ['어머니', '얼굴', '우리', 

In [47]:
df.columns

Index(['id', 'topic', 'text', 'keywords', 'keywords_tfid'], dtype='object')

In [48]:
df['keywords_tfid'] = keyword_list

In [49]:
df

id topic  \
0         NIRW1900000001.17    기술   
1        NIRW1900000001.215    기술   
2        NIRW1900000001.432    기술   
3        NIRW1900000001.552    기술   
4        NIRW1900000001.620    기술   
...                     ...   ...   
382508  NZRW2200000001.2200    기술   
382509  NZRW2200000001.2215    기술   
382510  NZRW2200000001.2222    기술   
382511  NZRW2200000001.2244    기술   
382512  NZRW2200000001.2256    기술   

                                                     text  \
0       모두에게 '윈-윈 게임'이 되는 세상, 아름다운 동행 21세기는 IQ(지능지수, I...   
1       자동차 타고 우주로 드라이브할까 날씨가 추워지면서 일상생활이 많이 움츠러든다. 바깥...   
2       독선과 아집은 왜 생기는 걸까? <팡세>에 관한 단상 1. "인간은 자연에서, 그것...   
3       "학업에 치친 청소년들도 멋진 별세계에 찾아오세요" 국내최초로 일반인들을 대상으로 ...   
4       '-의' 안 써야 우리 말이 깨끗하다 (247) ㄱ. 소비의 엄청난 증가로 인해 ....   
...                                                   ...   
382508  차별 확산 막는 AI 가이드라인 첫발 챗봇, 스피커 등 편의 도구에서 취업까지 인공...   
382509  방통위 “공영방송 협약제도 도입 추진” 방송통신위원회가 2022년 업무계획을 발표했...   
382510  지상파방송사들 “대기업 지분 소유 규제 풀어달라” 지상파 방송사들이 대기업의 지상파...   
382511  구독 정보 맞춤형 ‘이재명 정책 앱’ 파괴력 어느 정도일까 더불어민주당이 대선 정책...   
382512  국힘 “박성제 배임” MBC “지나친 비판” 공방 이유는 국민의힘이 방송 사유화를 ...   

                                                 keywords  \
0       ['지수', '사회', '공존', '사람', '지능지수', '능력', '위해', '...   
1       ['우주', '센터', '나로', '고흥', '나로도', '위성', '발사', '발...   
2       ['인간', '아집', '독선', '파스칼', '사회', '자신', '때문', '우...   
3       ['시민', '천문대', '천문학', '대해', '사람', '최초', '교육', '...   
4       ['주제', '감촉', '강의', '촉감', '오늘', '화석연료', '소비', '...   
...                                                   ...   
382508  ['가이드라인', '차별', '기술', '원칙', '개발', '활용', '의사결정'...   
382509  ['방송', '방통위', '제도', '위해', '공영', '추진', '마련', '허...   
382510  ['방송', '지상파', '기업', '소유', '자산', '시장', '제한', '기...   
382511  ['이재명', '민주당', '플러스', '콘텐츠', '소통', '플랫폼', '특보'...   
382512  ['사장', '스피커', '주장', '노출', '업체', '방송', '노동조합', ...   

                                         keywords_tfid  
0           [지수, 사회, 공존, 사람, 능력, 지능지수, 다른, 성공, 위해, 동행]  
1          [우주, 센터, 나로, 고흥, 나로도, 발사, 해변, 위성, 소록도, 발사체]  
2            [인간, 독선, 아집, 파스칼, 자신, 사회, 우주, 때문, 사람, 자연]  
3           [시민, 천문대, 천문학, 사람, 대해, 교육, 과장, 최초, 우주, 천문]  
4           [주제, 강의, 감촉, 촉감, 소비, 때문, 화석연료, 토씨, 한자, 증가]  
...                                                ...  
382508  [기술, 가이드라인, 차별, 활용, 사회, 원칙, 데이터, 인간, 의사결정, 개발]  
382509     [방송, 방통위, 위해, 공영, 마련, 제도, 사업자, 미디어, 허가, 재난]  
382510       [방송, 지상파, 기업, 소유, 자산, 시장, 규제, 기준, 제한, 주장]  
382511   [이재명, 민주당, 정보, 정책, 플러스, 콘텐츠, 플랫폼, 경제, 국민, 소통]  
382512     [사장, 스피커, 노출, 주장, 방송, 업체, 노조, 노동조합, 사옥, 업무]  

[382513 rows x 5 columns]

In [1]:
df.keywords_tfid[1]

NameError: name 'df' is not defined

In [54]:
df.to_csv(directory_path+'/news_T_two_keywords.tsv', sep='\t', index=False)